# Quickstart

`ipyannotations` doesn't have many components, so it should be fast
to get up to speed.

## Installation

Start by installing `ipyannotations`:

```
$ pip install ipyannotations
```

If you are using Jupyter Lab, rather than the old Jupyter Notebook application, you will also
have to install two Jupyter Lab extensions:

```
$ jupyter labextension install @jupyter-widgets/jupyterlab-manager ipycanvas
$ jupyter labextension install @jupyter-widgets/jupyterlab-manager
```


## Create a polygon annotation widget

A common use case for machine learning is to create polygon masks of objects in an image
you want to be able to detect.

To do so, you have to import the `PolygonAnnotator`, set the classes you want to annotate,
and then load your image:

In [1]:
from ipyannotations import PolygonAnnotator
widget = PolygonAnnotator(options=["eye", "mouth"])
widget.display("img/baboon.png")


To display the interactive annotation tool, you then simply need to place it at the end of the jupyter cell
(like with any other content in a jupyter notebook):

In [2]:
widget

PolygonAnnotator(children=(PolygonAnnotationCanvas(layout=Layout(height='500px', width='700px'), size=(700, 50…

To edit a created annoation, you can click the edit button,
which allows you to drag the points around. To make this
easier, you can use the "Point size" slider to increase the
points for easier clicking.

In [3]:
## hidden cell, not shown in nbsphinx
widget.canvas.data = [
   {'type': 'polygon',
    'label': 'eye',
    'points': [(253, 53),
    (250, 65),
    (261, 75),
    (279, 76),
    (292, 68),
    (295, 56),
    (287, 50),
    (270, 49),
    (257, 49),
    (253, 53)]},
    {'type': 'polygon',
    'label': 'eye',
    'points': [(411, 45),
    (421, 42),
    (440, 43),
    (450, 47),
    (452, 57),
    (442, 69),
    (430, 76),
    (412, 75),
    (401, 59),
    (403, 46),
    (411, 45)]}
]

widget.canvas[0].sync_image_data = True
widget.canvas[1].sync_image_data = True


## Access the data you have created

There are two ways of processing the annotations you have created. One is to access the
`widget.data` attribute, and either send your annotation to some database, or store it
locally:

In [4]:
from IPython.display import display
display(widget.data)

[{'type': 'polygon',
  'label': 'eye',
  'points': [(253, 53),
   (250, 65),
   (261, 75),
   (279, 76),
   (292, 68),
   (295, 56),
   (287, 50),
   (270, 49),
   (257, 49),
   (253, 53)]},
 {'type': 'polygon',
  'label': 'eye',
  'points': [(411, 45),
   (421, 42),
   (440, 43),
   (450, 47),
   (452, 57),
   (442, 69),
   (430, 76),
   (412, 75),
   (401, 59),
   (403, 46),
   (411, 45)]}]

In [5]:
import json
import pathlib
pathlib.Path("img/baboon.json").write_text(json.dumps(widget.data));


Another approach is to register a "submit" function, which is called
whenever a user presses the "Submit" button:

In [6]:
def store_annotations(data):
    pathlib.Path("img/baboon.json").write_text(json.dumps(widget.data))

widget.on_submit(store_annotations)

## Create other annotation widgets

The full list of annotation widgets as of now is:

1. `PolygonAnnotator`
2. `PointAnnotator`

Planned for the future:

- a `PixelAnnotator` which allows you to drag over pixels to mark them all as a class
- a `BoxAnnotator`, which allows you to create simple bounding boxes


### PolygonAnnotator

Polygons with an arbitrary number of points. Each polygon is formatted
as a dictionary with the keys:

```
{
    'type': 'polygon',
    'label': <class label>,
    'points': <list of xy-tuples>
}
```


In [7]:
polygon_widget = PolygonAnnotator(options=["eye", "mouth"])
polygon_widget.display("img/baboon.png")
polygon_widget

PolygonAnnotator(children=(PolygonAnnotationCanvas(layout=Layout(height='500px', width='700px'), size=(700, 50…

In [8]:
## hidden cell, not shown in nbsphinx
polygon_widget.canvas[0].sync_image_data = True
polygon_widget.canvas[1].sync_image_data = True


### PointAnnotator

Single point annotations, formatted as dictionaries with keys:

```
{
    'type': 'point',
    'label': <class label>,
    'points': <xy-tuple>
}
```


In [9]:
from ipyannotations import PointAnnotator
point_widget = PointAnnotator(options=["eye", "mouth"])
point_widget.display("img/baboon.png")
point_widget

PointAnnotator(children=(PointAnnotationCanvas(layout=Layout(height='500px', width='700px'), size=(700, 500)),…

In [10]:
## hidden cell, not shown in nbsphinx
point_widget.canvas[0].sync_image_data = True
point_widget.canvas[1].sync_image_data = True


In [11]:
## hidden cell, not shown in nbsphinx
from PIL import Image
import ipywidgets as widgets
import io

def patch_widget_for_canvas(annotator):
    im = Image.new("RGB", annotator.canvas.size, color=(255, 255, 255))
    im2 = Image.fromarray(annotator.canvas[0].get_image_data())
    im3 = Image.fromarray(annotator.canvas[1].get_image_data())
    im.paste(im2, mask=im2)
    im.paste(im3, mask=im3)
#     im = im.convert("RGB")
    buffer = io.BytesIO()
    im.save(buffer, format="JPEG", quality=75)
    img_widg = widgets.Image(
        value=buffer.getvalue()
    )

    annotator.children = (img_widg,) + annotator.children[1:]
    annotator.layout.width = annotator.children[1].layout.width
    # close these so the state doesn't get saved:
    for canvas in annotator.canvas:
        canvas.close()
    annotator.canvas.close()

patch_widget_for_canvas(widget)
patch_widget_for_canvas(polygon_widget)
patch_widget_for_canvas(point_widget)